In [ ]:
#@title Install Latest Version of Packages
!pip install --upgrade google-cloud-bigquery
!pip install --upgrade google-cloud-bigquery-storage
!pip install --upgrade pyarrow
!pip install --upgrade google-cloud-core
!pip install --upgrade chart_studio

In [1]:
# Basic Python data science libraries
import pandas as pd
import numpy as np
import scipy.optimize

# Import and setup for plotly in Colab
import chart_studio
import chart_studio.plotly as py
import plotly.graph_objects as go
import plotly.io as pio

# Enable extension package to display pandas data frames as interactive tables 
%load_ext google.colab.data_table

In [2]:
from google.colab import auth
auth.authenticate_user()
print('Authenticated')

Authenticated


In [3]:
project_id = 'tc-test-project-260312' #@param{type:"string"}

# Packages used for interfacing w/ BigQuery from Python
from google.cloud import bigquery
from google.cloud import bigquery_storage_v1beta1

# Create BigQuery client
bq_client = bigquery.Client(project = project_id)

# Create BigQuery storage client
bq_storage_client = bigquery_storage_v1beta1.BigQueryStorageClient()

In [53]:
#@title Get Weather Stations data from BigQuery
%%bigquery weather_stations --project {project_id}

#Select data beginning Jan 2000, with end date of June 30 2020 - require 95% valid dates in 2019
# Subquery to count # of dates w/ valid temperature data by station
WITH
Num2019TempDatesByStation AS
(
  SELECT
    daily_weather.stn,
  
    # Count # of distinct dates w/ temperature data for each station
    COUNT(DISTINCT
      # Convert year/month/day info into date
      DATE(
        CAST(daily_weather.year AS INT64),
        CAST(daily_weather.mo AS INT64),
        CAST(daily_weather.da AS INT64)
        )) AS num_2019_temp_dates,
        max(daily_weather.max) as max_temp_stn

  FROM
    `bigquery-public-data.noaa_gsod.gsod2019` daily_weather

  WHERE 
    daily_weather.temp IS NOT NULL AND
    daily_weather.max IS NOT NULL AND
    daily_weather.min IS NOT NULL AND
    # Remove days w/ missing temps coded as 99999.9
    daily_weather.temp != 9999.9 AND
    daily_weather.max != 9999.9 AND
    daily_weather.min != 9999.9

  GROUP BY
    daily_weather.stn
),

# Calculate max number of 2019 temperature dates across all stations
MaxNum2019TempDates AS
(
  SELECT
    MAX(num_2019_temp_dates) AS max_num_2019_temp_dates
  
  FROM
    Num2019TempDatesByStation
)

SELECT
  Stations.*,
  Num2019TempDatesByStation.num_2019_temp_dates,
  Num2019TempDatesByStation.max_temp_stn,
  MaxNum2019TempDates.max_num_2019_temp_dates,
  RANK () OVER ( PARTITION BY stations.country
		ORDER BY Num2019TempDatesByStation.max_temp_stn DESC
	) rank_no

FROM
  `bigquery-public-data.noaa_gsod.stations` Stations

# Inner join to filter to only stations present in 2019 data
INNER JOIN
  Num2019TempDatesByStation ON (
    stations.usaf = Num2019TempDatesByStation.stn
    )

# Cross join to get max number on each row, to use in filtering below
CROSS JOIN
  MaxNum2019TempDates

WHERE
  # Filter to stations that have had tracking since at least 1/1/2000
  Stations.begin <= '20100101' AND
  # Filter to stations that have had tracking through at least 6/30/2019
  Stations.end >= '20200630' AND
  # Filter to stations w/ >= 90% of the max number of dates for 2019
  Num2019TempDatesByStation.num_2019_temp_dates >= 
    (0.90 * MaxNum2019TempDates.max_num_2019_temp_dates)
    
ORDER BY
  stations.usaf

In [54]:
#@title Interactive Table of Weather Stations - Stations Ranked within Country
weather_stations

usaf   wban  ... max_num_2019_temp_dates rank_no
0     010010  99999  ...                     365     201
1     010020  99999  ...                     365     206
2     010030  99999  ...                     365     204
3     010060  99999  ...                     365     205
4     010070  99999  ...                     365       2
...      ...    ...  ...                     ...     ...
9462  999999  94088  ...                     365       5
9463  999999  94644  ...                     365       5
9464  999999  94645  ...                     365       5
9465  999999  94995  ...                     365       5
9466  999999  94996  ...                     365       5

[9467 rows x 15 columns]

In [55]:
#@title Extract the Station with the Max value for 2019 for each country
top_station_per_country = weather_stations[weather_stations['rank_no'] == 1]
top_station_per_country

usaf   wban  ... max_num_2019_temp_dates rank_no
5     010080  99999  ...                     365       1
56    011220  99999  ...                     365       1
245   021810  99999  ...                     365       1
540   029910  99999  ...                     365       1
586   032040  99999  ...                     365       1
...      ...    ...  ...                     ...     ...
9291  998229  99999  ...                     365       1
9304  998263  99999  ...                     365       1
9314  999999  64757  ...                     365       1
9315  999999  40504  ...                     365       1
9316  999999  40710  ...                     365       1

[245 rows x 15 columns]

In [64]:
top_station_NZ = weather_stations[(weather_stations['rank_no'] <= 10) & (weather_stations['country'] == 'NZ')]
top_station_NZ

usaf   wban  ... max_num_2019_temp_dates rank_no
8385  931860  99999  ...                     365       9
8388  932920  99999  ...                     365       4
8390  933730  99999  ...                     365       1
8395  934980  99999  ...                     365      10
8398  935460  99999  ...                     365       5
8401  936780  99999  ...                     365       8
8403  937730  99999  ...                     365       5
8404  937800  99999  ...                     365       2
8405  937810  99999  ...                     365       2
8410  938910  99999  ...                     365       7

[10 rows x 15 columns]

In [63]:
#Hotest temp in the world 2019
Hotest_station2019 = weather_stations.iloc[weather_stations['max_temp_stn'].idxmax()]
Hotest_station2019

usaf                                  690150
wban                                   93121
name                       TWENTY NINE PALMS
country                                   US
state                                     CA
call                                    KNXP
lat                                     34.3
lon                                 -116.167
elev                                 +0625.1
begin                               19900102
end                                 20200816
num_2019_temp_dates                      360
max_temp_stn                           129.9
max_num_2019_temp_dates                  365
rank_no                                    1
Name: 5205, dtype: object

In [65]:
#@title Choose Weather Station From My Home Town
chosen_station_usaf = "937730" #@param{type:"string"}

if chosen_station_usaf not in weather_stations['usaf'].tolist():
  print('Not a Valid USAF, Picking Random Weather Station Instead...')
  chosen_station_usaf = weather_stations['usaf'].sample(1).iloc[0]

# Filter to only chosen station
chosen_station_info = weather_stations[weather_stations['usaf'] == 
  chosen_station_usaf]

chosen_station_name = chosen_station_info['name'].iloc[0]

# Add station usaf to BigQuery parameters dictionary
bigquery_params = {
  "chosen_station_usaf": chosen_station_usaf
  }

print('Chosen Station: ' + chosen_station_name)
chosen_station_info

Chosen Station: TIMARU AERODROME AWS


usaf   wban  ... max_num_2019_temp_dates rank_no
8403  937730  99999  ...                     365       5

[1 rows x 15 columns]

In [67]:
#@title Get Daily Temperature Data for Timaru - 2019
%%bigquery chosen_station_daily_2019 --project {project_id} --params $bigquery_params

WITH CTE AS (  SELECT
  # Station information
  daily_weather.stn AS usaf,
  
  # Convert year/month/day info into date
  DATE(CAST(daily_weather.year AS INT64),CAST(daily_weather.mo AS INT64),CAST(daily_weather.da AS INT64)) AS date,
  
  daily_weather.temp AS avg_temp,
  daily_weather.count_temp AS n_for_avg_temp,
  
  daily_weather.max AS max_temp,
#flag_max - Blank indicates max temp was taken from the explicit max temp report and not from the 'hourly' data. 
#* indicates max temp was derived from the hourly data (i.e., highest hourly or synoptic-reported temperature)
  daily_weather.flag_max AS max_temp_flag,
  
  daily_weather.min AS min_temp,
#flag_min	- Blank indicates min temp was taken from the explicit min temp report and not from the 'hourly' data. 
#* indicates min temp was derived from the hourly data (i.e., lowest hourly or synoptic-reported temperature)
  daily_weather.flag_min AS min_temp_flag

FROM
  `bigquery-public-data.noaa_gsod.gsod2019` daily_weather

WHERE 
  # Filter to only chosen station
  daily_weather.stn = @chosen_station_usaf AND
  # Remove days w/ missing temps coded as 99999.9 (can throw off calculations)
  daily_weather.temp != 9999.9 AND
  daily_weather.max != 9999.9 AND
  daily_weather.min != 9999.9

ORDER BY
  date DESC
)


SELECT c1.*, #c2.avg_temp as prev_avg_temp,        
		ROUND(COALESCE (((c1.avg_temp - c2.avg_temp) * 1.0 / c2.avg_temp) * 100, 0),2) AS PercChange_PrevDay
FROM CTE AS c1  LEFT JOIN CTE AS c2 
ON c1.date = date_add(c2.date, interval 1 day)


In [69]:
#@title Table of Temperature Data for Timaru Airport
chosen_station_daily_2019

usaf        date  avg_temp  ...  min_temp  min_temp_flag PercChange_PrevDay
0    937730  2019-10-04      53.2  ...      31.3           None              18.49
1    937730  2019-09-18      44.5  ...      26.4           None               4.95
2    937730  2019-02-14      58.2  ...      54.5              *              -7.91
3    937730  2019-11-23      56.8  ...      51.1              *             -15.85
4    937730  2019-05-23      42.6  ...      34.2              *              -0.93
..      ...         ...       ...  ...       ...            ...                ...
357  937730  2019-02-04      62.4  ...      46.0           None               6.30
358  937730  2019-06-30      36.8  ...      28.4           None              -2.90
359  937730  2019-07-16      43.6  ...      35.4           None               5.06
360  937730  2019-11-10      49.9  ...      46.6              *             -23.35
361  937730  2019-10-19      52.0  ...      38.1           None              10.40

[362 rows x 9 columns]

In [70]:
#@title Plot of Timaru Daily Temperature - 2019

# Create table of temperature series to plot, with names, symbols, colors
daily_temp_plot_fields = pd.DataFrame.from_records(  
  columns = ['field_name', 'plot_label', 'marker_symbol', 'line_color', 
    'plot_mode'],
  data = [
    ('avg_temp', 'Avg', 'circle', None, 'markers'),
    ('max_temp', 'Max', 'triangle-up', None, 'markers'),
    ('min_temp', 'Min', 'triangle-down', None, 'markers')
    ]
  )

# Create function to plot single station daily temperature
def plot_single_station_daily_temp(daily_temp_data, plot_fields, station_name):
  daily_plot_data = []

  for index, row in plot_fields.iterrows():
    daily_plot_data = (daily_plot_data +
      [go.Scatter(
        x = daily_temp_data['date'],
        y = daily_temp_data[row['field_name']],
        name = row['plot_label'],
        marker = dict(
          # Constant color scale for plotting temp to use for all stations
          cmin = -22, # -22°F corresponds to -30°C (very cold, to most)
          cmax = 122, # 122°F corresponds to 50°C (very hot, to most)
          color = daily_temp_data[row['field_name']], 
          # colorscale = 'BlueReds',
          colorscale = [[0, 'rgb(0, 0, 230)'], [0.5, 'rgb(190, 190, 190)'],
            [1, 'rgb(230, 0, 0)']],
          symbol = row['marker_symbol']
          ),
        line = dict(
          color = row['line_color']
          ),
        mode = row['plot_mode']
        )]
      )

  daily_plot_layout = go.Layout(
    title = dict(
      text = (station_name + ' Daily Temperature'),
      xref = "paper", 
      x = 0.5
      ),
    yaxis = dict(title = 'Temperature (°F)')
    )

  pio.show(go.Figure(daily_plot_data, daily_plot_layout))

plot_single_station_daily_temp(chosen_station_daily_2019,
  daily_temp_plot_fields, chosen_station_name)

In [71]:
#@title Multi-Year Daily Temperature Data for Timaru
chosen_start_year = 2010 #@param{type:"integer"}

chosen_end_year = 2019 #@param{type:"integer"}

def get_single_station_daily_temp_multiple_yrs(station_usaf, start_year, 
  end_year):
  
  single_station_daily_weather_multiyear_union_sql = ("\nUNION ALL\n".
    join([('''
      ( SELECT * FROM `bigquery-public-data.noaa_gsod.gsod{year}`
      WHERE stn = '{station_usaf}')
      ''')
    .format(year = year, station_usaf = station_usaf)
       for year in np.arange(start_year, (end_year + 1))
    ]))

  single_station_daily_multiyear_sql = '''
    WITH
    daily_weather AS
    (
      {daily_weather_table}
    )

    SELECT
      daily_weather.stn AS usaf,
      
      # Convert year/month/day info into date
      DATE(
        CAST(daily_weather.year AS INT64),
        CAST(daily_weather.mo AS INT64),
        CAST(daily_weather.da AS INT64)
        ) AS date,
      
      daily_weather.temp AS avg_temp,
      daily_weather.count_temp AS n_for_avg_temp,
      
      daily_weather.max AS max_temp,
      daily_weather.flag_max AS max_temp_flag,
      
      daily_weather.min AS min_temp,
      daily_weather.flag_min AS min_temp_flag

    FROM
      daily_weather
    
    WHERE 
      # Remove days w/ missing temps coded as 99999.9 (can throw off calcs)
      daily_weather.temp != 9999.9 AND
      daily_weather.max != 9999.9 AND
      daily_weather.min != 9999.9

    ORDER BY
      date DESC
    '''

  single_station_daily_multiyear_query = (single_station_daily_multiyear_sql.
    format(
      daily_weather_table = single_station_daily_weather_multiyear_union_sql,
      station_usaf = station_usaf
      )
    )

  single_station_daily_multiyear_df = (bq_client.
    query(single_station_daily_multiyear_query).
    result().
    to_arrow(bqstorage_client = bq_storage_client).
    to_pandas()
    )

  return(single_station_daily_multiyear_df)

chosen_station_daily_multiyear = get_single_station_daily_temp_multiple_yrs(
  chosen_station_usaf, chosen_start_year, chosen_end_year    
  )

plot_single_station_daily_temp(chosen_station_daily_multiyear, 
  daily_temp_plot_fields, chosen_station_name)

In [72]:
#@title Fit a Sine Curve to Timaru Multi-Year Temperature Data
# Describe sinusoidal model as function w/ parameters of interest
def sine_function(t, amp, freq, phase_shift, mean):
  return (amp * np.sin(freq * 2 * np.pi * (t - phase_shift)) + mean)

# Fit sinusoidal model to data, return either fit info or daily temp estimates
def fit_sine_curve_to_daily_temp_data(daily_temp_data, temp_field_name,
  return_value = 'sine curve fit info'):

  # Calculate total range of days in data
  daily_temp_data['days_since_start'] = (daily_temp_data['date'] - 
    min(daily_temp_data['date'])).dt.days

  # Starting point for mean is mean of temp in data set
  guess_mean = daily_temp_data[temp_field_name].mean()
  
  # Starting point for amplitude is half diff btw 1st & 99th %tiles of temp
  guess_amp = (daily_temp_data[temp_field_name].quantile(0.99) -
    daily_temp_data[temp_field_name].quantile(0.01)) / 2

  # Starting point for frequency is inverse of avg # of days in year
  guess_freq = 1/365.25
  
  # Starting point for phase shift is +80 days (into spring, in most cases)
  guess_phase_shift = 80

  # Use curve fit optimizer on data, w/ above guesses as starting points
  sine_curve_fit = scipy.optimize.curve_fit(
    f = sine_function,
    xdata = np.array(daily_temp_data['days_since_start']),
    ydata = np.array(daily_temp_data[temp_field_name]),
    p0 = [guess_amp, guess_freq, guess_phase_shift, guess_mean]
    )

  # Extract estimated parameters from curve fit  
  est_amp, est_freq, est_phase_shift, est_mean = sine_curve_fit[0]

  # Use sine function & parameters to get daily estimates of average temperature
  daily_temp_data['est_' + temp_field_name] = sine_function(
    daily_temp_data['days_since_start'],
    est_amp, est_freq, est_phase_shift, est_mean
    )
  
  # Calculate mean absolute error of estimates vs actual temperature
  curve_estimate_mean_abs_err = abs(
    daily_temp_data['est_' + temp_field_name] - daily_temp_data[temp_field_name]
    ).mean()

  # Create data frame of sine curve fit info
  sine_curve_fit_info_df = pd.DataFrame(data = [{
    ('est_amp_' + temp_field_name): est_amp,
    ('est_freq_' + temp_field_name): est_freq,
    ('est_phase_shift_' + temp_field_name): est_phase_shift,
    ('est_mean_' + temp_field_name): est_mean,
    ('est_range_' + temp_field_name): 2 * abs(est_amp),
    ('mae_fitted_' + temp_field_name): curve_estimate_mean_abs_err
    }])
  
  # Return either sine curve fit into or daily temp data w/ estimates
  if(return_value == 'sine curve fit info'):
    return(sine_curve_fit_info_df)

  elif(return_value == 'daily temp data with estimates'):
    return(daily_temp_data)

In [79]:
#@title Calculate Estimated Avg Temp and Plot Alongside Actual Temp
# Use function to fit sine curve, get out daily temp estimates for given station
chosen_station_daily_temp_with_preds = fit_sine_curve_to_daily_temp_data(
  daily_temp_data = chosen_station_daily_multiyear, 
  temp_field_name = 'avg_temp',
  return_value = 'daily temp data with estimates'
  )

# Set up plot fields structure: points for actual temp, curve for estimated temp
daily_avg_and_estimate_plot_fields = pd.DataFrame.from_records(
  columns = ['field_name', 'plot_label', 'marker_symbol', 'line_color', 
    'plot_mode'],
  data = [
    ('avg_temp', 'Actual Avg', 'circle', None, 'markers'),
    ('est_avg_temp', 'Estimated Avg', None, 'purple', 'lines')
    ]
  )

# Use function to plot daily temperature with estimates for given station
plot_single_station_daily_temp(chosen_station_daily_temp_with_preds, 
  daily_avg_and_estimate_plot_fields, chosen_station_name)

In [80]:
#@title Calculate Estimated Max Temp and Plot Alongside Actual Max Temp 
# Use function to fit sine curve, get out daily temp estimates for given station
chosen_station_daily_temp_with_preds = fit_sine_curve_to_daily_temp_data(
  daily_temp_data = chosen_station_daily_multiyear, 
  temp_field_name = 'max_temp',
  return_value = 'daily temp data with estimates'
  )

# Set up plot fields structure: points for actual temp, curve for estimated temp
daily_avg_and_estimate_plot_fields_max = pd.DataFrame.from_records(
  columns = ['field_name', 'plot_label', 'marker_symbol', 'line_color', 
    'plot_mode'],
  data = [
    ('max_temp', 'Actual Max', 'circle', None, 'markers'),
    ('est_max_temp', 'Estimated Max', None, 'purple', 'lines')
    ]
  )

# Use function to plot daily temperature with estimates for given station
plot_single_station_daily_temp(chosen_station_daily_temp_with_preds, 
  daily_avg_and_estimate_plot_fields_max, chosen_station_name)

In [81]:
#@title Add Other Stations to Analysis
# Choose number of weather stations to sample (randomly) from above list
num_stations_to_sample = 4 #@param {type:"number"}

# Enter USAF #s of other weather stations to be included (quoted & separated by commas)
other_usafs_to_include = "['937730']" #@param {type:"string"}

# Seed for random # generation to ensure consistent sampling (reproducibility)
seed = 23 

chosen_weather_stations = pd.concat([
  # Randomly sample specified number of weather stations         
  weather_stations.sample(n = num_stations_to_sample, random_state = seed),
  # Filter to other specified stations provided in array of USAFs
  weather_stations.query("usaf in " + other_usafs_to_include)
  ],
  ignore_index = True
  # Might be duplicates if sampled & fixed stations overlap, so drop them
  ).drop_duplicates()

# Initialize list of sine curve fit info data frames
sine_curve_fit_info_df_collection = []

# Loop over data frame of chosen weather stations
for index, row in chosen_weather_stations.iterrows():
  # Use function to get daily temperature data for given station from BigQuery
  this_station_daily_temp_data = get_single_station_daily_temp_multiple_yrs(
    station_usaf = row['usaf'],
    start_year = chosen_start_year,
    end_year = chosen_end_year
    )
  
  # Don't count unless station has >=500 days of temperature data
  if(this_station_daily_temp_data.shape[0] < 500):
    # Print message and move on in this case
    print("Not Enough Temp Data for USAF " + row['usaf'] + ' ' + row['name'])
  
  # As long as station has >=500 days of temperature data
  else:
    # Use function to find sine curve fit for this station's temperature data
    this_station_temp_sine_curve_fit_info = fit_sine_curve_to_daily_temp_data(
      daily_temp_data = this_station_daily_temp_data,
      temp_field_name = 'avg_temp'
      )
    
    # Add station USAF and name to this fit into data frame
    this_station_temp_sine_curve_fit_info['station_usaf'] = row['usaf']
    this_station_temp_sine_curve_fit_info['station_name'] = row['name']

    # Add data frame for this station to collection for all stations
    sine_curve_fit_info_df_collection = (sine_curve_fit_info_df_collection +
      [this_station_temp_sine_curve_fit_info])

# Concatenate collection of all stations' data frames into 1 data frame
all_station_fit_info = pd.concat(sine_curve_fit_info_df_collection,
  ignore_index = True).set_index(['station_usaf', 'station_name']).reset_index()

# Look at interactive table of all station fit info
all_station_fit_info

station_usaf  ... mae_fitted_avg_temp
0       483290  ...            2.965637
1       013200  ...            4.604056
2       837460  ...            3.049834
3       359250  ...            6.749985
4       937730  ...            3.765139

[5 rows x 8 columns]

In [82]:
#@title Fitting a Sine Curve to Another Station
station_usaf = '359250' #@param{type:"string"}

# Message if station is not in our chosen set
if station_usaf not in chosen_weather_stations['usaf'].tolist():
  print('Not in Chosen Weather Stations')

# Message if station was in our chosen set, but not enough temperature data
elif station_usaf not in all_station_fit_info['station_usaf'].tolist():
  print('Not Enough Temp Data for USAF ' + station_usaf)

else:
  # Filter to only chosen station
  station_fit_info = all_station_fit_info[
    all_station_fit_info['station_usaf'] == station_usaf]

  # Print fit into
  print(station_fit_info.round(decimals = 4))

  # Extract weather station name
  station_name = station_fit_info['station_name'].iloc[0]

  # Use function to get daily temperature data for given station from BigQuery
  station_daily_temp_data = get_single_station_daily_temp_multiple_yrs(
    station_usaf = station_usaf,
    start_year = chosen_start_year,
    end_year = chosen_end_year
    )

  # Use function to find sine curve fit for this station's temperature data
  station_daily_temp_data_with_preds = fit_sine_curve_to_daily_temp_data(
    daily_temp_data = station_daily_temp_data,
    temp_field_name = 'avg_temp',
    return_value = 'daily temp data with estimates'
    )
  
  # Use function to plot given station's daily temperature with model estimates
  plot_single_station_daily_temp(station_daily_temp_data_with_preds, 
    daily_avg_and_estimate_plot_fields, station_name)

  station_usaf station_name  ...  est_range_avg_temp  mae_fitted_avg_temp
3       359250          SAM  ...             68.6485                 6.75

[1 rows x 8 columns]


In [83]:
#@title Write All Weather Station Data to BigQuery Table
output_dataset_id = 'weather_demo' #@param{type:'string'}

output_table_id = 'sample_weather_station_temp_curve_fit_info' #@param{type:'string'}

replace_or_append_output = 'replace' #@param{type:'string'} ['replace', 'append']

# Combine project and dataset
project_dataset = (bq_client.project + '.' + output_dataset_id)

# Check to make sure output dataset exists, create it if not
try:
 bq_client.get_dataset(output_dataset_id)
 print("Dataset " + project_dataset + " exists\n")
 
except:
 print("Dataset " + project_dataset + " doesn't exist, so creating it\n")
 dataset = bq_client.create_dataset(bigquery.Dataset(project_dataset))

job_config = bigquery.LoadJobConfig()

# Modify job config depending on if we want to replace or append to table
if(replace_or_append_output == 'replace'):
 job_config.write_disposition = bigquery.WriteDisposition.WRITE_TRUNCATE  
else:  
 job_config.write_disposition = bigquery.WriteDisposition.WRITE_APPEND

dataset_ref = bq_client.dataset(output_dataset_id)
table_ref = dataset_ref.table(output_table_id)

# Get timestamp (UTC), add to data frame at granularity of seconds
all_station_fit_info['timestamp'] = pd.Timestamp.now(tz = 'UTC').ceil(freq = 's'
 )

# Use client functionality to load BigQuery table from Pandas data frame
bq_client.load_table_from_dataframe(
 dataframe = all_station_fit_info,
 destination = table_ref,
 job_config = job_config
 ).result()
 
print('All Station Fit Info output (' + replace_or_append_output + ') to ' +
 project_dataset + '.' + output_table_id +
 '\n')

Dataset tc-test-project-260312.weather_demo exists

All Station Fit Info output (replace) to tc-test-project-260312.weather_demo.sample_weather_station_temp_curve_fit_info

